# Map Area - Seattle, Washington State, USA

I chose the Seattle area from OSM because I live here, and I was interested to see what contributions to OpenStreetMap were happening in my neighborhood. It turns out that one of the most frequent contributors was directly from my neighborhood!

I initially wanted to pull the premade map from Map Zen but the file was too large for the purpose of this project (over 1 GB when uncompressed). I instead made a custom Overpass API call to grab a smaller geographic area, which ended up being around 250 MB when uncompressed. 

# Problems Encountered

I generated csv files from the Seattle area map and imported them into SQL tables. After querying to find issues with the data, I utilized the sampling code provided with the project description with an initial parameter value of k=10 to grab a smaller chunk of the OpenStreetMap XML file. The auditing functions were tested on this smaller sample file. 

## Problem 1
The first problem I encountered was the issue of double entries in the 'ways_tags' table when the key value was 'street'. Conjoined values like ‘15TH Ave Northwest;15th Avenue Northwest’ as well as two completely different streetnames in the same entry were found (29 cases total). However, besides manually picking the best option for the way tag, I was not able to come up with a workable solution for the scope of this project - the only way to know which name was more appropriate was to have specific domain knowledge regarding the local geography. Maybe after the machine learning sections of this course I will have a better solution :-)

In [232]:
import csv

with open('ways_tags.csv', 'r') as csvfile:
    reader = csv.reader(csvfile, delimiter=',')
    problems = []
    for row in reader:
        #finding all entries in the 'value' column with double values and are relevant to street name info
        if (';' in row[2]) and (row[1] =='destination'):
            problems.append(row)
print(len(problems))

29


## Problem 2
I also noticed that the audit.py function was generating some redundant street types - namely, abbreviations like NW and NE were present in addition to Northwest and Northeast. There was also an unexplained 'n' type (someone had put n in the entry field). I updated the mapping dictionary to convert NW and NE to their full names and replaced these instances. I also converted n into a blank space to be stripped out later.

In [283]:
mapping = { "St": "Street",
           "St ":"Street",
            "St.": "Street",
            "Ave": "Avenue",
            "Rd.":"Road",
           "NW":"Northwest",
           "NE":"Northeast",
           "n":""
            }



def replace(name, mapping):
    elements = name.split()
    for i in range(len(elements)):
        if elements[i] in mapping:
            elements[i] = mapping[elements[i]]
            name = " ".join(elements)
        else:
            pass
    return name

## Problem 3
Finally, there were a few cases where the 4 digit trailing postal code was included, which I decided to remove to keep everything standardized.
```
sqlite> SELECT tags.value, COUNT(*) as count 
   ...> FROM (SELECT * FROM nodes_tags 
   ...>   UNION ALL 
   ...>       SELECT * FROM ways_tags) tags
   ...> WHERE tags.key='postcode'
   ...> GROUP BY tags.value
   ...> ORDER BY count DESC;
   
98133-9145,1
98144,1
98148,1
98165,1
98175,1
98195-2350,1```
   


In [234]:
def post_code_std(filename):
    for _, elem in ET.iterparse(filename):
        if elem.tag == 'tag' and elem.attrib['k'] == 'addr:postcode':
            elem.attrib['v'] = elem.attrib['v'][0:6]
            return(elem.attrib['v'])
        

In [235]:
post_code_std(OSMFILE)

'98133'

# Data Overview

### File Sizes

| File        | Size (MB)           |
| ------------- |:-------------:|
| seattle_osm      | 248.6  |
| sea_sample      | 25.1      |
| ways_nodes | 27.8      |
| ways_tags | 21.4 |
| ways| 7.6 |
|nodes_tags| 8 |
|nodes| 90.7 |


### Number of Unique Users
```sqlite>  SELECT COUNT(DISTINCT(X.uid))FROM (SELECT uid FROM nodes UNION ALL SELECT uid FROM ways) X;```
#### 604



### Number of Nodes and Ways
```sqlite> select count(*) from nodes;```
#### 1037655

```sqlite> select count(*) from ways;```
#### 122556



### Most Number of Nodes tagged shop

Surprisingly, the most common nodes tagged shop were hair and beauty stores. This could indicate that the openstreetmap data is not an accurate reflection of reality, or that people in Seattle are extremely concerned with their appearance!

```sqlite> select value, count(*) as count from nodes_tags where key='shop' group by value order by count desc limit 10;```

| Shop        | Count  |
| ------------- |:-------------:|
|hairdresser|119|
|beauty|93|
|clothes|89|
|convenience|51|
|dry_cleaning|37|
|yes|31|
|car_repair|30|
|furniture|29|
|books|25|
|mobile_phone|23|

The value of 'yes' for shops was puzzling and I did a little exploration to try and figure out what it meant. 

```
sqlite> select *, count(*) as count from nodes_tags where value = 'yes' group by key order by count desc limit 5;

4906728043,bus,yes,regular,1063
5156175491,tactile_paving,yes,regular,376
5063108926,entrance,yes,regular,319
5152668154,wheelchair,yes,regular,299
4775958454,shelter,yes,regular,192
```

After looking up tactile paving (from Wikipedia: 'textured ground surface indicator found on footpaths, stairs and train station platforms to assist pedestrians who are visually impaired'), I inferred that the 'yes' was referring to ADA compliance or something of that nature. So shops with 'yes' in the value column are ADA compliant


### Top contributing Users

```sqlite> select X.user, count(*) as count from (select user from nodes union all select user from ways) X group by X.user order by count desc limit 10;```

| User        | Contributions  |
| ------------- |:-------------:|
|SeattleImport|505639|
|Glassman|285451|
|seattlefyi|90379|
|Foundatron|61511|
|sctrojan79|41845|
|Sudobangbang|29661|
|"Ballard OpenStreetMap"|25448|
|lukobe|24647|
|_mapsam|11066|
|zephyr|6035|

Ballard is my neighborhood, and it was really cool to see the open street map project so strongly supported locally!

### Total number of tags


In [236]:
count_tags(OSMFILE)

{'node': 103766, 'nd': 114130, 'member': 2239, 'tag': 78216, 'relation': 101, 'way': 12256, 'osm': 1}


### Number of tag types

Seeing no problemchars tag types is reassuring - it means our cleaning step in the shape element function worked properly


In [237]:
process_map(OSMFILE)

{'problemchars': 0, 'lower': 34482, 'other': 784, 'lower_colon': 42950}


{'lower': 34482, 'lower_colon': 42950, 'other': 784, 'problemchars': 0}

# Conclusion & Additional Suggestions

I thought about ways to improve the quality of the data, and I felt that the issue of duplicated tags for street names might benefit from updating street names if there was construction or some kind of renaming event. I searched for tags related to construction and came up with around a dozen events, but they only seemed to indicate that construction was occuring. Maybe adding an additional attribute related to renaming would help resolve the double entry issue, although it would have to be widely adopted to be of more help than harm.

I also wondered about creating some kind of 'user' classes with perks and increased visibility as the amount of data contributed increases. I found that the distribution of contributions approximately followed a power law distribution, with a few users generating most of the data. For example, the top three contributors had 43.6%, 24.6%, and 7.8% of all entries respectively. That means 76% of the total data was generated by just these three users! I think creating a 'power user' class and some accompanying perks like free OSM swag and invitations to conferences/events would hopefully incentive people to become power users as well.

Overall it was really interesting getting a look at Seattle through the lens of publicly uploaded data - I noticed some quirks that spoke to the unique character of Seattle like the high amount of bike related data. I was happy to contribute a little bit to the OpenStreetMap Project.

### Problem 1 Appendix

The problem was discovered by querying SQL tables using: 
```
sqlite> select value, count(*) as count from ways_tags where key = 'street' group by value order by count asc limit 10;
"15TH Ave Northwest;15th Avenue Northwest",1
"15th Ave W",1
"17th Avenue Northeast;17th Place Northeast",1
"20th avenue nw",1
"22nd Ave NW",1
"22nd Avenue Northwest;Northwest 62nd Street",1
"25th Ave NE",1
"25th Ave NW",1
"3rd Place Northwest",1
"8th Place West",1
```


### Problem 2 & 3 Appendix

modified the shape element function to include cleaning both postal codes and updating street names

In [280]:
#NEW CLEANING PART - POSTAL CODE AND STREET NAMES
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
Created on Thu Oct 19 15:46:00 2017

@author: bfan
"""

###Prep for SQL###

import csv
import codecs
import pprint
import re
import xml.etree.cElementTree as ET

import cerberus

import schema

OSM_PATH = "/Users/bfan/Desktop/Udacity Course Materials/seattle_osm"

NODES_PATH = "nodes.csv"
NODE_TAGS_PATH = "nodes_tags.csv"
WAYS_PATH = "ways.csv"
WAY_NODES_PATH = "ways_nodes.csv"
WAY_TAGS_PATH = "ways_tags.csv"

LOWER_COLON = re.compile(r'^([a-z]|_)+:([a-z]|_)+')
PROBLEMCHARS = re.compile(r'[=\+/&<>;\'"\?%#$@\,\. \t\r\n]')

SCHEMA = schema = {
    'node': {
        'type': 'dict',
        'schema': {
            'id': {'required': True, 'type': 'integer', 'coerce': int},
            'lat': {'required': True, 'type': 'float', 'coerce': float},
            'lon': {'required': True, 'type': 'float', 'coerce': float},
            'user': {'required': True, 'type': 'string'},
            'uid': {'required': True, 'type': 'integer', 'coerce': int},
            'version': {'required': True, 'type': 'string'},
            'changeset': {'required': True, 'type': 'integer', 'coerce': int},
            'timestamp': {'required': True, 'type': 'string'}
        }
    },
    'node_tags': {
        'type': 'list',
        'schema': {
            'type': 'dict',
            'schema': {
                'id': {'required': True, 'type': 'integer', 'coerce': int},
                'key': {'required': True, 'type': 'string'},
                'value': {'required': True, 'type': 'string'},
                'type': {'required': True, 'type': 'string'}
            }
        }
    },
    'way': {
        'type': 'dict',
        'schema': {
            'id': {'required': True, 'type': 'integer', 'coerce': int},
            'user': {'required': True, 'type': 'string'},
            'uid': {'required': True, 'type': 'integer', 'coerce': int},
            'version': {'required': True, 'type': 'string'},
            'changeset': {'required': True, 'type': 'integer', 'coerce': int},
            'timestamp': {'required': True, 'type': 'string'}
        }
    },
    'way_nodes': {
        'type': 'list',
        'schema': {
            'type': 'dict',
            'schema': {
                'id': {'required': True, 'type': 'integer', 'coerce': int},
                'node_id': {'required': True, 'type': 'integer', 'coerce': int},
                'position': {'required': True, 'type': 'integer', 'coerce': int}
            }
        }
    },
    'way_tags': {
        'type': 'list',
        'schema': {
            'type': 'dict',
            'schema': {
                'id': {'required': True, 'type': 'integer', 'coerce': int},
                'key': {'required': True, 'type': 'string'},
                'value': {'required': True, 'type': 'string'},
                'type': {'required': True, 'type': 'string'}
            }
        }
    }
}

# Make sure the fields order in the csvs matches the column order in the sql table schema
NODE_FIELDS = ['id', 'lat', 'lon', 'user', 'uid', 'version', 'changeset', 'timestamp']
NODE_TAGS_FIELDS = ['id', 'key', 'value', 'type']
WAY_FIELDS = ['id', 'user', 'uid', 'version', 'changeset', 'timestamp']
WAY_TAGS_FIELDS = ['id', 'key', 'value', 'type']
WAY_NODES_FIELDS = ['id', 'node_id', 'position']

street_type_re = re.compile(r'\b\S+\.?$', re.IGNORECASE)


expected = ["Street", "Avenue", "Boulevard", "Drive", "Court", "Place", "Square", "Lane", "Road", 
            "Trail", "Parkway", "Commons", "Lane", 'Circle', 'East', "North", 'West', "South", 
            "Northwest", "Northeast", 'Way', "Esplanade", "Terrace"]

mapping = { "St": "Street",
           "St ":"Street",
            "St.": "Street",
            "Ave": "Avenue",
            "Rd.":"Road",
           "NW":"Northwest",
           "NE":"Northeast",
           "n":""
            }
def replace(name, mapping):
    elements = name.split()
    for i in range(len(elements)):
        if elements[i] in mapping:
            elements[i] = mapping[elements[i]]
            name = " ".join(elements)
        else:
            pass
    return name

def shape_element(element, node_attr_fields=NODE_FIELDS, way_attr_fields=WAY_FIELDS,
                  problem_chars=PROBLEMCHARS, default_tag_type='regular'):
    """Clean and shape node or way XML element to Python dict"""

    node_attribs = {}
    way_attribs = {}
    way_nodes = []
    tags = [] 
    

                    
    if element.tag == 'node':
        for attr in node_attr_fields:
            node_attribs[attr] = element.get(attr)
        for tag_entry in element.iter('tag'):
            tag = {}
            tag['id'] = element.attrib['id']
            #conditions for tag type
            problem = problem_chars.search(tag_entry.attrib['k'])
            if problem:
                continue
            else:
                key = LOWER_COLON.search(tag_entry.attrib['k'])
                if key:
                    tag_type = tag_entry.attrib['k'].split(':',1)[0]
                    tag_field = tag_entry.attrib['k'].split(':',1)[1]
                    tag['type'] = tag_type
                    tag['key'] = tag_field
                    #fixing postal codes
                    if tag_entry.attrib['k'] == 'addr:postcode':
                        tag['value'] = tag_entry.attrib['v'][0:6]
                    #replacing street names
                    elif tag_entry.attrib['k'] =='addr:street':
                        tag['value'] = replace(tag_entry.attrib['v'], mapping)
                    else:
                        tag['value']= tag_entry.attrib['v']
                else:
                    tag['type'] = default_tag_type
                    tag['key']= tag_entry.attrib['k']
                    if tag_entry.attrib['k'] == 'addr:postcode':
                        tag['value'] = tag_entry.attrib['v'][0:6]
                    elif tag_entry.attrib['k'] =='addr:street':
                        tag['value'] = replace(tag_entry.attrib['v'], mapping)
                    else:
                        tag['value']= tag_entry.attrib['v']
                    tag['value']= tag_entry.attrib['v']
            tags.append(tag)
        return {'node': node_attribs, 'node_tags': tags}
        
    elif element.tag == 'way':
        for attr in way_attr_fields:
            way_attribs[attr] = element.get(attr)
        for tag_entry in element.iter('tag'):
            tag = {}
            tag['id'] = element.attrib['id']
            #type conditions
            problem = problem_chars.search(tag_entry.attrib['k'])
            if problem:
                continue
            else:
                key = LOWER_COLON.search(tag_entry.attrib['k'])
                if key:
                    tag['type'] = tag_entry.attrib['k'].split(':',1)[0]
                    tag['key'] = tag_entry.attrib['k'].split(':',1)[1]
                    if tag_entry.attrib['k'] == 'addr:postcode':
                        tag['value'] = tag_entry.attrib['v'][0:6]
                    elif tag_entry.attrib['k'] =='addr:street':
                        tag['value'] = replace(tag_entry.attrib['v'], mapping)
                    else:
                        tag['value'] = tag_entry.attrib['v']                   
                else:
                    tag['type'] = default_tag_type
                    tag['key']= tag_entry.attrib['k']
                    if tag_entry.attrib['k'] == 'addr:postcode':
                        tag['value'] = tag_entry.attrib['v'][0:6]
                    elif tag_entry.attrib['k'] =='addr:street':
                        tag['value'] = replace(tag_entry.attrib['v'], mapping)
                    else:
                        tag['value']= tag_entry.attrib['v']
                    tag['value'] = tag_entry.attrib['v'] 
            tags.append(tag)
        count = 0
        for nd in element.iter('nd'):
            nd_entry = {}
            nd_entry['id'] = element.attrib['id']
            nd_entry['node_id'] = nd.attrib['ref']
            nd_entry['position'] = count
            count += 1
            way_nodes.append(nd_entry)

        return {'way': way_attribs, 'way_nodes': way_nodes, 'way_tags': tags}

### Supplementary Code Appendix

All functions used throughout project

In [249]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
Created on Thu Oct 19 15:42:26 2017

@author: bfan
"""

###Audit Street Names###

import xml.etree.cElementTree as ET
from collections import defaultdict
import re
import pprint

OSMFILE = "sea_sample.osm"
street_type_re = re.compile(r'\b\S+\.?$', re.IGNORECASE)


expected = ["Street", "Avenue", "Boulevard", "Drive", "Court", "Place", "Square", "Lane", "Road", 
            "Trail", "Parkway", "Commons", "Lane", 'Circle', 'East', "North", 'West', "South", 
            "Northwest", "Northeast", 'Way', "Esplanade", "Terrace"]

# UPDATE THIS VARIABLE
mapping = { "St": "Street",
           "St ":"Street",
            "St.": "Street",
            "Ave": "Avenue",
            "Rd.":"Road",
           "NW":"Northwest",
           "NE":"Northeast",
           "n":""
            }



def audit_street_type(street_types, street_name):
    m = street_type_re.search(street_name)
    if m:
        street_type = m.group()
        if street_type not in expected:
            if street_type in mapping:
                new_type = update_name(street_type,mapping)
                street_types[new_type].add(new_type)
            else:
                street_types[street_type].add(street_name)


def is_street_name(elem):
    return (elem.attrib['k'] == "addr:street")


def audit(osmfile):
    osm_file = open(osmfile, "r")
    street_types = defaultdict(set)
    for event, elem in ET.iterparse(osm_file, events=("start",)):

        if elem.tag == "node" or elem.tag == "way":
            for tag in elem.iter("tag"):
                if is_street_name(tag):
                    audit_street_type(street_types, tag.attrib['v'])
    osm_file.close()
    return street_types


def update_name(name, mapping):
    m = street_type_re.search(name)
    print (name)
    if m:
        street_type = m.group()
        if name not in expected:
            name = re.sub(street_type_re, mapping[street_type] , name)
    return name


lower = re.compile(r'^([a-z]|_)*$')
lower_colon = re.compile(r'^([a-z]|_)*:([a-z]|_)*$')
problemchars = re.compile(r'[=\+/&<>;\'"\?%#$@\,\. \t\r\n]')

def key_type(element, keys):
    if element.tag == "tag":
        value = element.attrib['k']
        if re.search(lower, value):
            keys['lower'] +=1 
        elif re.search(lower_colon, value):
            keys['lower_colon'] += 1
        elif re.search(problemchars, value):
            keys['problemchars'] += 1
        else:
            keys['other'] += 1
    print(keys)
    print('\n')# YOUR CODE HERE
    return keys

def process_map(filename):
    keys = {"lower": 0, "lower_colon": 0, "problemchars": 0, "other": 0}
    for _, element in ET.iterparse(filename):
        keys = key_type(element, keys)
    return keys

def count_tags(filename):
        tags = {}
        for event, element in ET.iterparse(filename):
            if element.tag in tags:
                tags[element.tag] +=1
            else:
                tags[element.tag] = 1
        print(tags)

In [262]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
Created on Thu Oct 19 15:46:12 2017

@author: bfan
"""


# ================================================== #
#               Helper Functions                     #
# ================================================== #
def get_element(osm_file, tags=('node', 'way', 'relation')):
    """Yield element if it is the right type of tag"""

    context = ET.iterparse(osm_file, events=('start', 'end'))
    _, root = next(context)
    for event, elem in context:
        if event == 'end' and elem.tag in tags:
            yield elem
            root.clear()


def validate_element(element, validator, schema=SCHEMA):
    """Raise ValidationError if element does not match schema"""
    if validator.validate(element, schema) is not True:
        field, errors = next(validator.errors.iteritems())
        message_string = "\nElement of type '{0}' has the following errors:\n{1}"
        error_string = pprint.pformat(errors)
        
        raise Exception(message_string.format(field, error_string))


class UnicodeDictWriter(csv.DictWriter, object):
    """Extend csv.DictWriter to handle Unicode input"""

    def writerow(self, row):
        super(UnicodeDictWriter, self).writerow({
            k: (v.encode('utf-8') if isinstance(v, unicode) else v) for k, v in row.iteritems()
        })

    def writerows(self, rows):
        for row in rows:
            self.writerow(row)

In [282]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
Created on Thu Oct 19 15:46:06 2017

@author: bfan
"""



import unicodecsv as csv
import codecs
# ================================================== #
#               Main Function                        #
# ================================================== #
def process_map(file_in, validate):
    """Iteratively process each XML element and write to csv(s)"""

    with codecs.open(NODES_PATH, 'w') as nodes_file, \
         codecs.open(NODE_TAGS_PATH, 'w') as nodes_tags_file, \
         codecs.open(WAYS_PATH, 'w') as ways_file, \
         codecs.open(WAY_NODES_PATH, 'w') as way_nodes_file, \
         codecs.open(WAY_TAGS_PATH, 'w') as way_tags_file:

        nodes_writer = UnicodeDictWriter(nodes_file, NODE_FIELDS)
        node_tags_writer = UnicodeDictWriter(nodes_tags_file, NODE_TAGS_FIELDS)
        ways_writer = UnicodeDictWriter(ways_file, WAY_FIELDS)
        way_nodes_writer = UnicodeDictWriter(way_nodes_file, WAY_NODES_FIELDS)
        way_tags_writer = UnicodeDictWriter(way_tags_file, WAY_TAGS_FIELDS)

        nodes_writer.writeheader()
        node_tags_writer.writeheader()
        ways_writer.writeheader()
        way_nodes_writer.writeheader()
        way_tags_writer.writeheader()

        validator = cerberus.Validator()

        for element in get_element(file_in, tags=('node', 'way')):
            el = shape_element(element)
            if el:
                if validate is True:
                    validate_element(el, validator)

                if element.tag == 'node':
                    nodes_writer.writerow(el['node'])
                    node_tags_writer.writerows(el['node_tags'])
                elif element.tag == 'way':
                    ways_writer.writerow(el['way'])
                    way_nodes_writer.writerows(el['way_nodes'])
                    way_tags_writer.writerows(el['way_tags'])


if __name__ == '__main__':
    # Note: Validation is ~ 10X slower. For the project consider using a small
    # sample of the map when validating.
    process_map(OSMFILE, validate=True)

{'changeset': '38737522', 'uid': '2814663', 'timestamp': '2016-04-20T19:36:43Z', 'version': '9', 'user': 'Ballard OpenStreetMap', 'id': '4635028'}


[{'position': 0, 'node_id': '29447670', 'id': '4635028'}, {'position': 1, 'node_id': '29449876', 'id': '4635028'}, {'position': 2, 'node_id': '29449875', 'id': '4635028'}, {'position': 3, 'node_id': '4136765589', 'id': '4635028'}, {'position': 4, 'node_id': '4136765591', 'id': '4635028'}, {'position': 5, 'node_id': '29449874', 'id': '4635028'}, {'position': 6, 'node_id': '4136765590', 'id': '4635028'}, {'position': 7, 'node_id': '29449873', 'id': '4635028'}, {'position': 8, 'node_id': '29449871', 'id': '4635028'}]
{'changeset': '37658530', 'uid': '2601744', 'timestamp': '2016-03-07T05:35:09Z', 'version': '8', 'user': 'sctrojan79', 'id': '4637363'}


[{'position': 0, 'node_id': '29484803', 'id': '4637363'}, {'position': 1, 'node_id': '1864943621', 'id': '4637363'}, {'position': 2, 'node_id': '29484804', 'id': '4637363'}, {'position': 3, 'no

{'changeset': '44383419', 'uid': '2601744', 'timestamp': '2016-12-13T21:06:02Z', 'version': '14', 'user': 'sctrojan79', 'id': '4921233'}


[{'position': 0, 'node_id': '2776431139', 'id': '4921233'}, {'position': 1, 'node_id': '1726011302', 'id': '4921233'}, {'position': 2, 'node_id': '4340674159', 'id': '4921233'}, {'position': 3, 'node_id': '1726056715', 'id': '4921233'}, {'position': 4, 'node_id': '4340674158', 'id': '4921233'}]
{'changeset': '36847965', 'uid': '2601744', 'timestamp': '2016-01-27T23:51:38Z', 'version': '23', 'user': 'sctrojan79', 'id': '4921402'}


[{'position': 0, 'node_id': '2542469035', 'id': '4921402'}, {'position': 1, 'node_id': '30012801', 'id': '4921402'}]
{'changeset': '18360744', 'uid': '1751737', 'timestamp': '2013-10-15T01:04:01Z', 'version': '4', 'user': 'Skybunny', 'id': '4921456'}


[{'position': 0, 'node_id': '32271380', 'id': '4921456'}, {'position': 1, 'node_id': '2496883177', 'id': '4921456'}]
{'changeset': '42090702', 'uid': '2601744', 'timestamp':

{'changeset': '49263151', 'uid': '1330847', 'timestamp': '2017-06-05T09:04:55Z', 'version': '20', 'user': 'TheDutchMan13', 'id': '6359036'}


[{'position': 0, 'node_id': '53079376', 'id': '6359036'}, {'position': 1, 'node_id': '2492766432', 'id': '6359036'}, {'position': 2, 'node_id': '59711148', 'id': '6359036'}, {'position': 3, 'node_id': '59711149', 'id': '6359036'}, {'position': 4, 'node_id': '4694838341', 'id': '6359036'}, {'position': 5, 'node_id': '59711150', 'id': '6359036'}, {'position': 6, 'node_id': '4694838339', 'id': '6359036'}, {'position': 7, 'node_id': '53067169', 'id': '6359036'}, {'position': 8, 'node_id': '3874895442', 'id': '6359036'}, {'position': 9, 'node_id': '59711152', 'id': '6359036'}, {'position': 10, 'node_id': '1726018771', 'id': '6359036'}, {'position': 11, 'node_id': '1726018774', 'id': '6359036'}, {'position': 12, 'node_id': '53098996', 'id': '6359036'}, {'position': 13, 'node_id': '3874891885', 'id': '6359036'}, {'position': 14, 'node_id': '3874891878',

{'changeset': '49263151', 'uid': '1330847', 'timestamp': '2017-06-05T09:05:35Z', 'version': '9', 'user': 'TheDutchMan13', 'id': '6372064'}


[{'position': 0, 'node_id': '53114497', 'id': '6372064'}, {'position': 1, 'node_id': '53114498', 'id': '6372064'}]
{'changeset': '49263151', 'uid': '1330847', 'timestamp': '2017-06-05T09:05:38Z', 'version': '5', 'user': 'TheDutchMan13', 'id': '6372589'}


[{'position': 0, 'node_id': '53115216', 'id': '6372589'}, {'position': 1, 'node_id': '53081100', 'id': '6372589'}]
{'changeset': '49305432', 'uid': '689176', 'timestamp': '2017-06-06T13:22:27Z', 'version': '14', 'user': 'pathym', 'id': '6373869'}


[{'position': 0, 'node_id': '1708652290', 'id': '6373869'}, {'position': 1, 'node_id': '67507166', 'id': '6373869'}, {'position': 2, 'node_id': '4840612149', 'id': '6373869'}, {'position': 3, 'node_id': '53116764', 'id': '6373869'}, {'position': 4, 'node_id': '4840633106', 'id': '6373869'}, {'position': 5, 'node_id': '1708652607', 'id': '6373869'}, {'p

[{'position': 0, 'node_id': '53156108', 'id': '6406449'}, {'position': 1, 'node_id': '67539561', 'id': '6406449'}, {'position': 2, 'node_id': '67539567', 'id': '6406449'}, {'position': 3, 'node_id': '53156110', 'id': '6406449'}, {'position': 4, 'node_id': '67539584', 'id': '6406449'}, {'position': 5, 'node_id': '67539576', 'id': '6406449'}, {'position': 6, 'node_id': '67539571', 'id': '6406449'}, {'position': 7, 'node_id': '53103660', 'id': '6406449'}, {'position': 8, 'node_id': '67539520', 'id': '6406449'}, {'position': 9, 'node_id': '53156111', 'id': '6406449'}, {'position': 10, 'node_id': '67539513', 'id': '6406449'}, {'position': 11, 'node_id': '1709188067', 'id': '6406449'}]
{'changeset': '49295005', 'uid': '1330847', 'timestamp': '2017-06-06T06:45:24Z', 'version': '4', 'user': 'TheDutchMan13', 'id': '6407542'}


[{'position': 0, 'node_id': '53091189', 'id': '6407542'}, {'position': 1, 'node_id': '53157331', 'id': '6407542'}, {'position': 2, 'node_id': '53157333', 'id': '6407542'}

...

{'changeset': '50736907', 'uid': '2814663', 'timestamp': '2017-08-01T02:16:32Z', 'version': '1', 'user': 'Ballard OpenStreetMap', 'id': '511868474'}


[{'position': 0, 'node_id': '5006166822', 'id': '511868474'}, {'position': 1, 'node_id': '5006166823', 'id': '511868474'}, {'position': 2, 'node_id': '5006166824', 'id': '511868474'}, {'position': 3, 'node_id': '5006166825', 'id': '511868474'}]
{'changeset': '50737323', 'uid': '2814663', 'timestamp': '2017-08-01T03:00:15Z', 'version': '1', 'user': 'Ballard OpenStreetMap', 'id': '511875029'}


[{'position': 0, 'node_id': '5006202100', 'id': '511875029'}, {'position': 1, 'node_id': '5006202101', 'id': '511875029'}, {'position': 2, 'node_id': '5006202102', 'id': '511875029'}]
{'changeset': '50759522', 'uid': '2814663', 'timestamp': '2017-08-01T17:50:34Z', 'version': '1', 'user': 'Ballard OpenStreetMap', 'id': '512111656'}


[{'position': 0, 'node_id': '5007860580', 'id': '512111656'}, {'position': 1, 'node_id': '5007860581', 'id': '51211165

{'changeset': '51093241', 'uid': '2814663', 'timestamp': '2017-08-13T21:27:05Z', 'version': '1', 'user': 'Ballard OpenStreetMap', 'id': '515356607'}


[{'position': 0, 'node_id': '5033157589', 'id': '515356607'}, {'position': 1, 'node_id': '5033157590', 'id': '515356607'}, {'position': 2, 'node_id': '5033157591', 'id': '515356607'}, {'position': 3, 'node_id': '5033157592', 'id': '515356607'}, {'position': 4, 'node_id': '5033157593', 'id': '515356607'}, {'position': 5, 'node_id': '5033157594', 'id': '515356607'}, {'position': 6, 'node_id': '5033157595', 'id': '515356607'}, {'position': 7, 'node_id': '5033157596', 'id': '515356607'}, {'position': 8, 'node_id': '5033157597', 'id': '515356607'}]
{'changeset': '51094791', 'uid': '2814663', 'timestamp': '2017-08-13T23:37:47Z', 'version': '1', 'user': 'Ballard OpenStreetMap', 'id': '515371878'}


[{'position': 0, 'node_id': '5033302909', 'id': '515371878'}, {'position': 1, 'node_id': '5033302908', 'id': '515371878'}]
{'changeset': '51094841',

{'changeset': '51792749', 'uid': '2814663', 'timestamp': '2017-09-06T20:27:41Z', 'version': '1', 'user': 'Ballard OpenStreetMap', 'id': '521921314'}


[{'position': 0, 'node_id': '5084620304', 'id': '521921314'}, {'position': 1, 'node_id': '5084620303', 'id': '521921314'}, {'position': 2, 'node_id': '5084620302', 'id': '521921314'}, {'position': 3, 'node_id': '5084620301', 'id': '521921314'}, {'position': 4, 'node_id': '5084620300', 'id': '521921314'}, {'position': 5, 'node_id': '5084620299', 'id': '521921314'}, {'position': 6, 'node_id': '5084620298', 'id': '521921314'}, {'position': 7, 'node_id': '5084620297', 'id': '521921314'}, {'position': 8, 'node_id': '5084620296', 'id': '521921314'}, {'position': 9, 'node_id': '5084620295', 'id': '521921314'}, {'position': 10, 'node_id': '5084620294', 'id': '521921314'}, {'position': 11, 'node_id': '5084620293', 'id': '521921314'}, {'position': 12, 'node_id': '5084620304', 'id': '521921314'}]
{'changeset': '51827765', 'uid': '137875', 'timestam


[{'position': 0, 'node_id': '504892542', 'id': '527113591'}, {'position': 1, 'node_id': '504892544', 'id': '527113591'}, {'position': 2, 'node_id': '504892543', 'id': '527113591'}, {'position': 3, 'node_id': '508037691', 'id': '527113591'}, {'position': 4, 'node_id': '508037705', 'id': '527113591'}, {'position': 5, 'node_id': '3697606292', 'id': '527113591'}, {'position': 6, 'node_id': '504886127', 'id': '527113591'}, {'position': 7, 'node_id': '504886125', 'id': '527113591'}, {'position': 8, 'node_id': '508037686', 'id': '527113591'}, {'position': 9, 'node_id': '53017945', 'id': '527113591'}, {'position': 10, 'node_id': '507971197', 'id': '527113591'}, {'position': 11, 'node_id': '53017948', 'id': '527113591'}, {'position': 12, 'node_id': '3697606304', 'id': '527113591'}, {'position': 13, 'node_id': '508037731', 'id': '527113591'}, {'position': 14, 'node_id': '504886128', 'id': '527113591'}, {'position': 15, 'node_id': '2983963969', 'id': '527113591'}, {'position': 16, 'node_id': '50


[{'position': 0, 'node_id': '5154329335', 'id': '530905456'}, {'position': 1, 'node_id': '5154329338', 'id': '530905456'}, {'position': 2, 'node_id': '5154329340', 'id': '530905456'}, {'position': 3, 'node_id': '5154329337', 'id': '530905456'}, {'position': 4, 'node_id': '5154329345', 'id': '530905456'}, {'position': 5, 'node_id': '5154329341', 'id': '530905456'}, {'position': 6, 'node_id': '5154329334', 'id': '530905456'}, {'position': 7, 'node_id': '4824960036', 'id': '530905456'}]
{'changeset': '52719480', 'uid': '2773196', 'timestamp': '2017-10-07T23:18:36Z', 'version': '1', 'user': 'NickBolten', 'id': '530907921'}


[{'position': 0, 'node_id': '5154343574', 'id': '530907921'}, {'position': 1, 'node_id': '5154343553', 'id': '530907921'}, {'position': 2, 'node_id': '5154343561', 'id': '530907921'}]
{'changeset': '52719503', 'uid': '2773196', 'timestamp': '2017-10-07T23:22:04Z', 'version': '1', 'user': 'NickBolten', 'id': '530908397'}


[{'position': 0, 'node_id': '5154345385', 'id'

SQL query to check number of 'construction' related tags

```
sqlite> SELECT tags.value, COUNT(*) as count 
   ...> FROM (SELECT * FROM nodes_tags UNION ALL 
   ...>       SELECT * FROM ways_tags) tags
   ...> WHERE tags.key LIKE ‘%construction’
   ...> GROUP BY tags.value
   ...> ORDER BY count DESC;

light_rail,7
university,3
yes,3
footway,2
residential,2
secondary_link,2
steps,2
subway,2
unclassified,2
building,1
minor,1
```
